<p align="center">
    <picture>
    <source media="(prefers-color-scheme: dark)" srcset="https://docs.nerf.studio/en/latest/_images/logo-dark.png">
    <source media="(prefers-color-scheme: light)" srcset="https://docs.nerf.studio/en/latest/_images/logo.png">
    <img alt="nerfstudio" src="https://docs.nerf.studio/en/latest/_images/logo.png" width="400">
    </picture>
</p>


# Nerfstudio: A collaboration friendly studio for NeRFs


![GitHub stars](https://img.shields.io/github/stars/nerfstudio-project/nerfstudio?color=gold&style=social)

This colab shows how to train and view NeRFs from Nerfstudio both on pre-made datasets or from your own videos/images.

\\

Credit to [NeX](https://nex-mpi.github.io/) for Google Colab format.

## Frequently Asked Questions

*  **Downloading custom data is stalling (no output):**
    * This is a bug in Colab. The data is processing, but may take a while to complete. You will know processing completed if `data/nerfstudio/custom_data/transforms.json` exists. Terminating the cell early will result in not being able to train.
*  **Processing custom data is taking a long time:**
    * The time it takes to process data depends on the number of images and its resolution. If processing is taking too long, try lowering the resolution of your custom data.
*  **Error: Data processing did not complete:**
    * This means that the data processing script did not fully complete. This could be because there were not enough images, or that the images were of low quality. We recommend images with little to no motion blur and lots of visual overlap of the scene to increase the chances of successful processing.
*   **Training is not showing progress**:
    * The lack of output is a bug in Colab. You can see the training progress from the viewer.
* **Viewer Quality is bad / Low resolution**:
    * This may be because more GPU is being used on training that rendering the viewer. Try pausing training or decreasing training utilization.
* **WARNING: Running pip as the 'root' user...:**:
    * This and other pip warnings or errors can be safely ignored.
* **Other problems?**
    * Feel free to create an issue on our [GitHub repo](https://github.com/nerfstudio-project/nerfstudio).


In [2]:
!pip install -q condacolab
import condacolab
condacolab.install()


✨🍰✨ Everything looks OK!


In [3]:
# !pip uninstall torch torchvision functorch tinycudann
# !pip install torch==2.0.1+cu118 torchvision==0.15.2+cu118 --extra-index-url https://download.pytorch.org/whl/cu118

In [1]:
#@markdown <h1> Downloading and Processing Data</h1>
#@markdown <h3>Pick the preset scene or upload your own images/video</h3>
import os
import glob
from google.colab import files
from IPython.core.display import display, HTML

scene = '\uD83D\uDDBC poster' #@param ['🖼 poster', '🚜 dozer', '🌄 desolation', '📤 upload your images' , '🎥 upload your own video', '🔺 upload Polycam data', '💽 upload your own Record3D data']
scene = ' '.join(scene.split(' ')[1:])

if scene == "upload Polycam data":
    %cd /content/
    !mkdir -p /content/data/nerfstudio/custom_data
    %cd /content/data/nerfstudio/custom_data/
    uploaded = files.upload()
    dir = os.getcwd()
    if len(uploaded.keys()) > 1:
        print("ERROR, upload a single .zip file when processing Polycam data")
    dataset_dir = [os.path.join(dir, f) for f in uploaded.keys()][0]
    !ns-process-data polycam --data $dataset_dir --output-dir /content/data/nerfstudio/custom_data/
    scene = "custom_data"
elif scene == 'upload your own Record3D data':
    display(HTML('<h3>Zip your Record3D folder, and upload.</h3>'))
    display(HTML('<h3>More information on Record3D can be found <a href="https://docs.nerf.studio/en/latest/quickstart/custom_dataset.html#record3d-capture" target="_blank">here</a>.</h3>'))
    %cd /content/
    !mkdir -p /content/data/nerfstudio/custom_data
    %cd /content/data/nerfstudio/custom_data/
    uploaded = files.upload()
    dir = os.getcwd()
    preupload_datasets = [os.path.join(dir, f) for f in uploaded.keys()]
    record_3d_zipfile = preupload_datasets[0]
    !unzip $record_3d_zipfile -d /content/data/nerfstudio/custom_data
    custom_data_directory = glob.glob('/content/data/nerfstudio/custom_data/*')[0]
    !ns-process-data record3d --data $custom_data_directory --output-dir /content/data/nerfstudio/custom_data/
    scene = "custom_data"
elif scene in ['upload your images', 'upload your own video']:
    display(HTML('<h3>Select your custom data</h3>'))
    display(HTML('<p/>You can select multiple images by pressing ctrl, cmd or shift and click.<p>'))
    display(HTML('<p/>Note: This may take time, especially on higher resolution inputs, so we recommend to download dataset after creation.<p>'))
    !mkdir -p /content/data/nerfstudio/custom_data
    if scene == 'upload your images':
        !mkdir -p /content/data/nerfstudio/custom_data/raw_images
        %cd /content/data/nerfstudio/custom_data/raw_images
        uploaded = files.upload()
        dir = os.getcwd()
    else:
        %cd /content/data/nerfstudio/custom_data/
        uploaded = files.upload()
        dir = os.getcwd()
    preupload_datasets = [os.path.join(dir, f) for f in uploaded.keys()]
    del uploaded
    %cd /content/

    if scene == 'upload your images':
        !ns-process-data images --data /content/data/nerfstudio/custom_data/raw_images --output-dir /content/data/nerfstudio/custom_data/
    else:
        video_path = preupload_datasets[0]
        !ns-process-data video --data $video_path --output-dir /content/data/nerfstudio/custom_data/

    scene = "custom_data"
else:
    %cd /content/
    !ns-download-data nerfstudio --capture-name=$scene

print("Data Processing Succeeded!")

/content
Downloading...
From (uriginal): https://drive.google.com/uc?id=1dmjWGXlJnUxwosN6MVooCDQe970PkD-1
From (redirected): https://drive.google.com/uc?id=1dmjWGXlJnUxwosN6MVooCDQe970PkD-1&confirm=t&uuid=9e6c06fe-9ebe-4d95-a5b7-b10701001180
To: /content/data/nerfstudio/poster.zip
100% 750M/750M [00:08<00:00, 87.4MB/s]
Data Processing Succeeded!


In [ ]:
# Activate conda environment
!conda create --name nerfstudio -y python=3.8
!conda activate nerfstudio
!python -m pip install --upgrade pip

# Install torch
!pip install torch==2.0.1+cu118 torchvision==0.15.2+cu118 --extra-index-url https://download.pytorch.org/whl/cu118

# Install cuda 11.8
!conda install -c "nvidia/label/cuda-11.8.0" cuda-toolkit

# Install tiny-cuda-nn
!pip install ninja git+https://github.com/NVlabs/tiny-cuda-nn/#subdirectory=bindings/torch

# Install NeRF Studio
!pip install git+https://github.com/nerfstudio-project/nerfstudio.git


In [96]:
!ls data/nerfstudio/$scene/

base_cam.json  colmap  images  images_2  images_4  images_8  transforms.json


In [97]:
!ls data/nerfstudio/$scene/images_4

frame_00001.png  frame_00058.png  frame_00115.png  frame_00172.png
frame_00002.png  frame_00059.png  frame_00116.png  frame_00173.png
frame_00003.png  frame_00060.png  frame_00117.png  frame_00174.png
frame_00004.png  frame_00061.png  frame_00118.png  frame_00175.png
frame_00005.png  frame_00062.png  frame_00119.png  frame_00176.png
frame_00006.png  frame_00063.png  frame_00120.png  frame_00177.png
frame_00007.png  frame_00064.png  frame_00121.png  frame_00178.png
frame_00008.png  frame_00065.png  frame_00122.png  frame_00179.png
frame_00009.png  frame_00066.png  frame_00123.png  frame_00180.png
frame_00010.png  frame_00067.png  frame_00124.png  frame_00181.png
frame_00011.png  frame_00068.png  frame_00125.png  frame_00182.png
frame_00012.png  frame_00069.png  frame_00126.png  frame_00183.png
frame_00013.png  frame_00070.png  frame_00127.png  frame_00184.png
frame_00014.png  frame_00071.png  frame_00128.png  frame_00185.png
frame_00015.png  frame_00072.png  frame_00129.png  frame_00186

In [98]:
!head -49  data/nerfstudio/$scene/transforms.json

{
  "fl_x": 1147.1526990016812,
  "fl_y": 1158.8252259026597,
  "k1": -0.013472197525381842,
  "k2": 0.007509466554079491,
  "p1": -0.0011800209664517077,
  "p2": 0.01116939407701522,
  "cx": 540.0,
  "cy": 960.0,
  "w": 1080,
  "h": 1920,
  "aabb_scale": 16,
  "frames": [
    {
      "file_path": "./images/frame_00001.png",
      "transform_matrix": [
        [
          0.32316911338447335, -0.8052290294881217, -0.4971598678734143,
          -0.7282161659858809
        ],
        [
          -0.43978339113907267, 0.33738608648128665, -0.8323227724429142,
          -2.7487404236023076
        ],
        [
          0.8379452804524355, 0.48762366505170673, -0.24509359079549578,
          -2.1384913608645126
        ],
        [0.0, 0.0, 0.0, 1.0]
      ]
    },
    {
      "file_path": "./images/frame_00004.png",
      "transform_matrix": [
        [
          0.27957346018561896, -0.7588883546911335, -0.5881557153288784,
          -0.9229457870819726
        ],
        [
          -0.

In [108]:
#@markdown <h1>Set up and Start Viewer</h1>

%cd /content

# Install localtunnel
# We are using localtunnel https://github.com/localtunnel/localtunnel but ngrok could also be used
!npm install -g localtunnel

# Tunnel port 7007, the default for
!rm url.txt 2> /dev/null
get_ipython().system_raw('lt --port 7007 >> url.txt 2>&1 &')

import time
time.sleep(3) # the previous command needs time to write to url.txt


with open('url.txt') as f:
  lines = f.readlines()
websocket_url = lines[0].split(": ")[1].strip().replace("https", "wss")

url = f"https://viewer.nerf.studio/?websocket_url={websocket_url}"
print(url)
print("You may need to click Refresh Page after you start training!")
from IPython import display
display.IFrame(src=url, height=800, width="100%")

/content
/tools/node/bin/lt -> /tools/node/lib/node_modules/localtunnel/bin/lt.js
+ localtunnel@2.0.2
updated 1 package in 1.515s
https://viewer.nerf.studio/?websocket_url=wss://true-plums-sneeze.loca.lt
You may need to click Refresh Page after you start training!


In [109]:
#@markdown <h1>Start Training</h1>
# instant-ngp
# nerfacto --pipeline.model.predict-normals True
# lerf-lite

%cd /content
if os.path.exists(f"data/nerfstudio/{scene}/transforms.json"):
    !ns-train lerf-lite --viewer.websocket-port 7007 nerfstudio-data \
       --data data/nerfstudio/$scene \
       --downscale-factor 4
else:
    from IPython.core.display import display, HTML
    display(HTML('<h3 style="color:red">Error: Data processing did not complete</h3>'))
    display(HTML('<h3>Please re-run `Downloading and Processing Data`, or view the FAQ for more info.</h3>'))

Streaming output truncated to the last 5000 lines.
Viewer at: https://viewer.nerf.studio/versions/23-05-15-1/?websocket_url=ws://localhost:7007         
Step (% Done)       Train Iter (time)    ETA (time)           Train Rays / Sec                       
-----------------------------------------------------------------------------------                  
26370 (87.90%)      95.239 ms            5 m, 45 s            43.08 K                                
26380 (87.93%)      96.083 ms            5 m, 47 s            42.71 K                                
26390 (87.97%)      97.112 ms            5 m, 50 s            42.28 K                                
26400 (88.00%)      96.053 ms            5 m, 45 s            42.74 K                                
26410 (88.03%)      96.602 ms            5 m, 46 s            42.49 K                                
26420 (88.07%)      96.519 ms            5 m, 45 s            42.54 K                                
26430 (88.10%)      94.470 ms  

In [63]:
import json
x = json.load(open('data/nerfstudio/poster/transforms.json'))


KeyError: ignored

In [1]:
#@title # Render Video { vertical-output: true }
#@markdown <h3>Export the camera path from within the viewer, then run this cell.</h3>
#@markdown <h5>The rendered video should be at renders/output.mp4!</h5>


base_dir = "/content/outputs/unnamed/nerfacto/"
training_run_dir = base_dir + os.listdir(base_dir)[-1]

from IPython.core.display import display, HTML
display(HTML('<h3>Upload the camera path JSON.</h3>'))
%cd $training_run_dir
uploaded = files.upload()
uploaded_camera_path_filename = list(uploaded.keys())[0]

config_filename = training_run_dir + "/config.yml"
camera_path_filename = training_run_dir + "/" + uploaded_camera_path_filename
camera_path_filename = camera_path_filename.replace(" ", "\\ ").replace("(", "\\(").replace(")", "\\)")

%cd /content/
!ns-render camera-path --load-config $config_filename --camera-path-filename $camera_path_filename --output-path renders/output.mp4

NameError: ignored

In [ ]:
from google.colab import files

files.download('renders/output.mp4')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
%cd /content
base_dir = "/content/outputs/unnamed/nerfacto/"
training_run_dir = base_dir + os.listdir(base_dir)[-1]
config_filename = training_run_dir + "/config.yml"

!ns-export poisson --load-config $config_filename --output-dir $base_dir

/content
Setting up training dataset...
Caching all 204 images.
Loading data batch ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
Setting up evaluation dataset...
Caching all 22 images.
Loading data batch ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100% 0:00:00
tiny-cuda-nn warning: FullyFusedMLP is not supported for the selected architecture 70. Falling back to CutlassMLP. For maximum performance, raise the target GPU architecture to 75+.
tiny-cuda-nn warning: FullyFusedMLP is not supported for the selected architecture 70. Falling back to CutlassMLP. For maximum performance, raise the target GPU architecture to 75+.
tiny-cuda-nn warning: FullyFusedMLP is not supported for the selected architecture 70. Falling back to CutlassMLP. For maximum performance, raise the target GPU architecture to 75+.
tiny-cuda-nn warning: FullyFusedMLP is not supported for the selected architecture 70. Falling back to CutlassMLP. For maximum performance, raise the target GPU architecture to 75+.
tiny-c

In [ ]:
from google.colab import files

for m in ['mesh.obj', 'material_0.mtl', 'material_0.png']:
  files.download(f'{base_dir}/{m}')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>